In [1]:
import nltk
from nltk.corpus import stopwords
from nltk.cluster.util import cosine_distance
import numpy as np
import networkx as nx

In [2]:
import pandas as pd
import numpy as np 
import os

In [3]:
trainse = pd.read_csv('../input/train_2.csv')
testse = pd.read_csv('../input/test_2.csv')

trainse = trainse.fillna('be well')

train = trainse[['text']]
test = testse[['text']]

In [4]:
trainse.drop(['text'],axis=1,inplace=True)
testse.drop(['text'],axis=1,inplace=True)

In [5]:
train['word_count'] = train['text'].str.split().map(len)
g = train[(train['word_count']>=1000)]
train = pd.concat([train, g]).drop_duplicates(keep=False)
train.drop(['word_count'],axis=1,inplace=True)

/opt/conda/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


In [6]:
test['word_count'] = test['text'].str.split().map(len)
h = test[(test['word_count']>=1000)]
test = pd.concat([test, h]).drop_duplicates(keep=False)
test.drop(['word_count'],axis=1,inplace=True)

In [7]:
def read_article(file_name):
    filedata = file_name
    article = filedata.split(".")
    print(article)

    sentences = []

    for sentence in article:
        #print(sentence)
        sentences.append(sentence.replace("[^a-zA-Z]", " ").split(" "))
    sentences.pop() 
    
    return sentences

In [8]:
def sentence_similarity(sent1, sent2, stopwords=None):
    if stopwords is None:
        stopwords = []
 
    sent1 = [w.lower() for w in sent1]
    sent2 = [w.lower() for w in sent2]
 
    all_words = list(set(sent1 + sent2))
 
    vector1 = [0] * len(all_words)
    vector2 = [0] * len(all_words)
 
    # build the vector for the first sentence
    for w in sent1:
        vector1[all_words.index(w)] += 1
 
    # build the vector for the second sentence
    for w in sent2:
        vector2[all_words.index(w)] += 1
 
    return 1 - cosine_distance(vector1, vector2)

In [9]:
def build_similarity_matrix(sentences, stop_words):
    # Create an empty similarity matrix
    similarity_matrix = np.zeros((len(sentences), len(sentences)))
 
    for idx1 in range(len(sentences)):
        for idx2 in range(len(sentences)):
            if idx1 == idx2: #ignore if both are same sentences
                continue 
            similarity_matrix[idx1][idx2] = sentence_similarity(sentences[idx1], sentences[idx2], stop_words)

    return similarity_matrix


In [10]:
def generate_summary(data):
    
    newly_col=[]
    for sentence in data:
        nltk.download("stopwords")
        stop_words = stopwords.words('english')
        summarize_text = []

    # Step 1 - Read text anc split it
        sentences =  read_article(sentence)
        top_n = int(len(sentences)/16)

    # Step 2 - Generate Similary Martix across sentences
        sentence_similarity_martix = build_similarity_matrix(sentences, stop_words)

    # Step 3 - Rank sentences in similarity martix
        sentence_similarity_graph = nx.from_numpy_array(sentence_similarity_martix)
        scores = nx.pagerank(sentence_similarity_graph)

    # Step 4 - Sort the rank and pick top sentences
        ranked_sentence = sorted(((scores[i],s) for i,s in enumerate(sentences)), reverse=True)       

        for i in range(top_n):
            summarize_text.append(" ".join(ranked_sentence[i][1]))
    
        newly_col.append(summarize_text)
    
    return newly_col

In [11]:
newly_train = generate_summary(g['text'])
newly_test = generate_summary(h['text'])

[nltk_data] Downloading package stopwords to /usr/share/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
['multiple sclerosis can be thought of as inflammatory process involving different areas of central nervous system at various points in time ', 'what causes this disease ? cause of multiple sclerosis is not known ', 'both environmental and genetic factors are thought to predispose person to develop disease ', 'multiple sclerosis results in destruction of myelin that surrounds nerves of cns ', 'myelin is fatty substance that insulates nerves and allows them to transmit information to and from brain ', 'if myelin is damaged , transmitted information is not only delayed but also may be misinterpreted by brain ', "myelin destruction , also known as demyelination , is thought to be caused by body ' immune cells entering cns ", 'disruption of normal barrier to entry of these cells , termed bloodbrain barrier , leads to local swelling ', 'also damaged are nerve cell bodi

In [12]:
g['newly'] = newly_train
h['newly'] = newly_test

In [13]:
def don(d):
    n=[]
    for s in d:
        res = ".".join(s)
        n.append(res)
    return n  

In [14]:
g['text'] = don(g['newly'])
h['text'] = don(h['newly'])

In [15]:
g.drop(['newly','word_count'],axis=1,inplace=True)
h.drop(['newly','word_count'],axis=1,inplace=True)

In [16]:
train2 = pd.merge(train,g,right_index=True,left_index=True,how='outer')
test2 = pd.merge(test,h,right_index=True,left_index=True,how='outer')

In [17]:
train2 = train2.fillna('')
train2['text'] = train2['text_x']+train2['text_y'] 

train2.drop(['text_x','text_y'],axis=1,inplace=True)

test2 = test2.fillna('')
test2['text'] = test2['text_x']+test2['text_y'] 

test2.drop(['text_x','text_y'],axis=1,inplace=True)

In [18]:
train = pd.merge(trainse,train2,right_index=True,left_index=True,how='inner')
test = pd.merge(testse,test2,right_index=True,left_index=True,how='inner')

In [19]:
train.to_csv('train_3.csv',index=False)
test.to_csv('test_3.csv',index=False)